In [1]:
!git clone https://github.com/mueedurrehman/distiller.git
%cd distiller
!pip3 install -e .

Cloning into 'distiller'...
remote: Enumerating objects: 5, done.
remote: Counting objects: 100% (5/5), done.
remote: Compressing objects: 100% (5/5), done.
remote: Total 6163 (delta 0), reused 1 (delta 0), pack-reused 6158
Receiving objects: 100% (6163/6163), 39.83 MiB | 34.98 MiB/s, done.
Resolving deltas: 100% (4319/4319), done.
/content/distiller
Obtaining file:///content/distiller
     |████████████████████████████████| 2.1MB 17.4MB/s 
     |████████████████████████████████| 734.6MB 24kB/s 
     |████████████████████████████████| 10.2MB 23.6MB/s 
     |████████████████████████████████| 460kB 55.8MB/s 
     |████████████████████████████████| 110.5MB 43kB/s 
     |████████████████████████████████| 51kB 9.3MB/s 
     |████████████████████████████████| 798kB 44.8MB/s 
     |████████████████████████████████| 112kB 58.4MB/s 
     |████████████████████████████████| 1.7MB 51.6MB/s 
     |████████████████████████████████| 235kB 61.6MB/s 
     |████████████████████████████████| 153kB 53.0MB

In [1]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [2]:
import torch
import torchvision
import torchvision.transforms as transforms
import torchvision.models as models
from torchsummary import summary
import matplotlib.pyplot as plt
import numpy as np
import torch.nn as nn
import torch.nn.functional as F
import time
import math
import yaml
import distiller
from collections import OrderedDict
import os
import pandas as pd

70% Restore

In [ ]:
!python3 /content/distiller/examples/classifier_compression/compress_classifier.py -a resnet56_cifar --compress="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Pruning Schedules/MSMG Schedules/20x4G0.85Restore0.7/threshold0S.yaml" ./data --resume="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Baseline Models/baseResnet56" -o "/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Pruning Schedules/MSMGResults" --epochs 100 --vs=0 --lr=0.08

Streaming output truncated to the last 5000 lines.
| 31 | module.layer2.5.conv2.weight        | (32, 32, 3, 3) |          9216 |           3395 |    0.00000 |    0.00000 |  0.00000 |  9.57031 |  0.00000 |   63.16189 | 0.04545 | -0.00375 |    0.02558 |
| 32 | module.layer2.6.conv1.weight        | (32, 32, 3, 3) |          9216 |           4753 |    0.00000 |    0.00000 |  0.00000 |  2.24609 |  0.00000 |   48.42665 | 0.06044 | -0.00597 |    0.03909 |
| 33 | module.layer2.6.conv2.weight        | (32, 32, 3, 3) |          9216 |           2292 |    0.00000 |    0.00000 |  0.00000 | 23.53516 |  0.00000 |   75.13021 | 0.04039 |  0.00095 |    0.01887 |
| 34 | module.layer2.7.conv1.weight        | (32, 32, 3, 3) |          9216 |           4132 |    0.00000 |    0.00000 |  0.00000 |  6.83594 |  0.00000 |   55.16493 | 0.05261 | -0.00615 |    0.03195 |
| 35 | module.layer2.7.conv2.weight        | (32, 32, 3, 3) |          9216 |           2702 |    0.00000 |    0.00000 |  0.00000 | 23.14453 |  0

In [ ]:
!python3 /content/distiller/examples/classifier_compression/compress_classifier.py -a resnet56_cifar --compress="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Pruning Schedules/MSMG Schedules/20x4G0.85Restore0.7/threshold0S.yaml" ./data --resume="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Baseline Models/baseResnet56" -o "/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Pruning Schedules/MSMGResults" --epochs 100 --vs=0 --lr=0.03

Streaming output truncated to the last 5000 lines.
| 32 | module.layer2.6.conv1.weight        | (32, 32, 3, 3) |          9216 |           5341 |    0.00000 |    0.00000 |  0.00000 |  0.87891 |  0.00000 |   42.04644 | 0.06279 | -0.00656 |    0.04282 |
| 33 | module.layer2.6.conv2.weight        | (32, 32, 3, 3) |          9216 |           2759 |    0.00000 |    0.00000 |  0.00000 | 18.45703 |  0.00000 |   70.06293 | 0.04293 |  0.00044 |    0.02204 |
| 34 | module.layer2.7.conv1.weight        | (32, 32, 3, 3) |          9216 |           4694 |    0.00000 |    0.00000 |  0.00000 |  5.46875 |  0.00000 |   49.06684 | 0.05405 | -0.00602 |    0.03477 |
| 35 | module.layer2.7.conv2.weight        | (32, 32, 3, 3) |          9216 |           3207 |    0.00000 |    0.00000 |  0.00000 | 18.65234 |  0.00000 |   65.20182 | 0.03916 | -0.00046 |    0.02128 |
| 36 | module.layer2.8.conv1.weight        | (32, 32, 3, 3) |          9216 |           5514 |    0.00000 |    0.00000 |  0.00000 |  9.57031 |  6

In [ ]:
!python3 /content/distiller/examples/classifier_compression/compress_classifier.py -a resnet56_cifar --compress="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Pruning Schedules/MSMG Schedules/20x4G0.85Restore0.7/threshold0-1S.yaml" ./data --resume="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Baseline Models/baseResnet56" -o "/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Pruning Schedules/MSMGResults" --epochs 100 --vs=0 --lr=0.08

Streaming output truncated to the last 5000 lines.
| 32 | module.layer2.6.conv1.weight        | (32, 32, 3, 3) |          9216 |           3376 |    0.00000 |    0.00000 |  0.00000 |  8.69141 |  0.00000 |   63.36806 | 0.05881 | -0.00497 |    0.03289 |
| 33 | module.layer2.6.conv2.weight        | (32, 32, 3, 3) |          9216 |           1708 |    0.00000 |    0.00000 |  0.00000 | 33.59375 |  0.00000 |   81.46701 | 0.03883 |  0.00069 |    0.01583 |
| 34 | module.layer2.7.conv1.weight        | (32, 32, 3, 3) |          9216 |           2788 |    0.00000 |    0.00000 |  0.00000 | 16.40625 |  0.00000 |   69.74826 | 0.05074 | -0.00452 |    0.02594 |
| 35 | module.layer2.7.conv2.weight        | (32, 32, 3, 3) |          9216 |           2383 |    0.00000 |    0.00000 |  0.00000 | 26.26953 |  0.00000 |   74.14280 | 0.03728 | -0.00020 |    0.01755 |
| 36 | module.layer2.8.conv1.weight        | (32, 32, 3, 3) |          9216 |           3271 |    0.00000 |    0.00000 |  0.00000 | 16.21094 |  9

In [ ]:
!python3 /content/distiller/examples/classifier_compression/compress_classifier.py -a resnet56_cifar --compress="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Pruning Schedules/MSMG Schedules/20x4G0.85Restore0.7/threshold0-1S.yaml" ./data --resume="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Baseline Models/baseResnet56" -o "/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Pruning Schedules/MSMGResults" --epochs 100 --vs=0 --lr=0.03

Streaming output truncated to the last 5000 lines.
| 32 | module.layer2.6.conv1.weight        | (32, 32, 3, 3) |          9216 |           3896 |    0.00000 |    0.00000 |  0.00000 |  6.54297 |  0.00000 |   57.72569 | 0.06119 | -0.00539 |    0.03680 |
| 33 | module.layer2.6.conv2.weight        | (32, 32, 3, 3) |          9216 |           2122 |    0.00000 |    0.00000 |  0.00000 | 29.00391 |  0.00000 |   76.97483 | 0.04112 |  0.00066 |    0.01874 |
| 34 | module.layer2.7.conv1.weight        | (32, 32, 3, 3) |          9216 |           3261 |    0.00000 |    0.00000 |  0.00000 | 13.86719 |  0.00000 |   64.61589 | 0.05220 | -0.00522 |    0.02893 |
| 35 | module.layer2.7.conv2.weight        | (32, 32, 3, 3) |          9216 |           2822 |    0.00000 |    0.00000 |  0.00000 | 22.46094 |  0.00000 |   69.37934 | 0.03870 | -0.00047 |    0.01987 |
| 36 | module.layer2.8.conv1.weight        | (32, 32, 3, 3) |          9216 |           3736 |    0.00000 |    0.00000 |  0.00000 | 13.28125 |  9

In [ ]:
!python3 /content/distiller/examples/classifier_compression/compress_classifier.py -a resnet56_cifar --compress="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Pruning Schedules/MSMG Schedules/20x4G0.85Restore0.7/threshold0-5S.yaml" ./data --resume="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Baseline Models/baseResnet56" -o "/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Pruning Schedules/MSMGResults" --epochs 100 --vs=0 --lr=0.08

Streaming output truncated to the last 5000 lines.
| 32 | module.layer2.6.conv1.weight        | (32, 32, 3, 3) |          9216 |           2298 |    0.00000 |    0.00000 |  0.00000 | 20.60547 |  0.00000 |   75.06510 | 0.05663 | -0.00400 |    0.02652 |
| 33 | module.layer2.6.conv2.weight        | (32, 32, 3, 3) |          9216 |           1126 |    0.00000 |    0.00000 |  0.00000 | 49.90234 |  0.00000 |   87.78212 | 0.03675 |  0.00069 |    0.01224 |
| 34 | module.layer2.7.conv1.weight        | (32, 32, 3, 3) |          9216 |           1682 |    0.00000 |    0.00000 |  0.00000 | 33.78906 |  3.12500 |   81.74913 | 0.04762 | -0.00361 |    0.01923 |
| 35 | module.layer2.7.conv2.weight        | (32, 32, 3, 3) |          9216 |           1005 |    0.00000 |    0.00000 |  3.12500 | 55.46875 |  0.00000 |   89.09505 | 0.03272 | -0.00003 |    0.01024 |
| 36 | module.layer2.8.conv1.weight        | (32, 32, 3, 3) |          9216 |           2207 |    0.00000 |    0.00000 |  0.00000 | 26.75781 |  9

In [ ]:
!python3 /content/distiller/examples/classifier_compression/compress_classifier.py -a resnet56_cifar --compress="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Pruning Schedules/MSMG Schedules/20x4G0.85Restore0.7/threshold0-5S.yaml" ./data --resume="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Baseline Models/baseResnet56" -o "/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Pruning Schedules/MSMGResults" --epochs 100 --vs=0 --lr=0.03

In [3]:
!python3 /content/distiller/examples/classifier_compression/compress_classifier.py -a resnet56_cifar --compress="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Pruning Schedules/MSMG Schedules/20x4G0.85Restore0.7/threshold1S.yaml" ./data --resume="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Baseline Models/baseResnet56" -o "/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Pruning Schedules/MSMGResults" --epochs 100 --vs=0 --lr=0.08

Streaming output truncated to the last 5000 lines.
| 32 | module.layer2.6.conv1.weight        | (32, 32, 3, 3) |          9216 |           1743 |    0.00000 |    0.00000 |  0.00000 | 27.83203 |  0.00000 |   81.08724 | 0.05452 | -0.00287 |    0.02236 |
| 33 | module.layer2.6.conv2.weight        | (32, 32, 3, 3) |          9216 |            955 |    0.00000 |    0.00000 |  0.00000 | 54.58984 |  0.00000 |   89.63759 | 0.03600 |  0.00109 |    0.01103 |
| 34 | module.layer2.7.conv1.weight        | (32, 32, 3, 3) |          9216 |           1506 |    0.00000 |    0.00000 |  0.00000 | 38.18359 |  3.12500 |   83.65885 | 0.04749 | -0.00314 |    0.01812 |
| 35 | module.layer2.7.conv2.weight        | (32, 32, 3, 3) |          9216 |            973 |    0.00000 |    0.00000 |  3.12500 | 55.07812 |  0.00000 |   89.44227 | 0.03315 | -0.00005 |    0.01021 |
| 36 | module.layer2.8.conv1.weight        | (32, 32, 3, 3) |          9216 |           1886 |    0.00000 |    0.00000 |  0.00000 | 32.03125 |  9

In [ ]:
!python3 /content/distiller/examples/classifier_compression/compress_classifier.py -a resnet56_cifar --compress="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Pruning Schedules/MSMG Schedules/20x4G0.85Restore0.7/threshold1S.yaml" ./data --resume="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Baseline Models/baseResnet56" -o "/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Pruning Schedules/MSMGResults" --epochs 100 --vs=0 --lr=0.03

Streaming output truncated to the last 5000 lines.
| 32 | module.layer2.6.conv1.weight        | (32, 32, 3, 3) |          9216 |           2082 |    0.00000 |    0.00000 |  0.00000 | 24.60938 |  0.00000 |   77.40885 | 0.05604 | -0.00339 |    0.02533 |
| 33 | module.layer2.6.conv2.weight        | (32, 32, 3, 3) |          9216 |           1170 |    0.00000 |    0.00000 |  0.00000 | 49.41406 |  0.00000 |   87.30469 | 0.03683 |  0.00112 |    0.01264 |
| 34 | module.layer2.7.conv1.weight        | (32, 32, 3, 3) |          9216 |           1758 |    0.00000 |    0.00000 |  0.00000 | 33.39844 |  3.12500 |   80.92448 | 0.04785 | -0.00328 |    0.01996 |
| 35 | module.layer2.7.conv2.weight        | (32, 32, 3, 3) |          9216 |           1155 |    0.00000 |    0.00000 |  3.12500 | 52.05078 |  0.00000 |   87.46745 | 0.03339 |  0.00021 |    0.01132 |
| 36 | module.layer2.8.conv1.weight        | (32, 32, 3, 3) |          9216 |           2218 |    0.00000 |    0.00000 |  0.00000 | 27.34375 |  9